In [1]:
import pandas as pd
import os 
import seaborn as sns
import numpy as np
import matplotlib.pyplot as plt
from datetime import datetime,date,timedelta
import pyodbc as odbc
import seaborn as sns
# Names the needed driver, server name, and database
driver_name='SQL Server'
server_name='10.0.1.218'
database='ritascoolnet_live'
#Creates the connection string
connection_string=f"""
DRIVER={{{driver_name}}};
SERVER={server_name};
DATABASE={database};
Trust_Connection=yes"""
#Creates the Connection to SQL Server
connection=odbc.connect(connection_string)
print(connection)

In [ ]:
#Queries the tables from SQL
#Reads in the Daily Sales from 2023
data1=pd.read_sql_query('''SELECT * FROM [dbo].[smartDailySales] Where Year(dteDate)>=2017''',connection)
#Reads in the Google Map to be able to join the inStoreID to the RitasID
data2=pd.read_sql_query('''Select intStoreID, intRitasStoreID as ShopID, vchStoreState,vchStoreName,dteReopenDate from ritascoolnet_live.dbo.GOOGLE_MAP_store''',connection)
# Pulls Marketing info needed like Coolnet Group, MSA, and DMA
data4=pd.read_sql_query('''Select intstoreid as intStoreID,RitasID, FC,CoolNetGroup,LegacyStoreType,State,MSAName,DMA,StoreName as ShopName,CoOpName from ritascoolnet_live.dbo.vShopDetail''',
                        connection)
gc=pd.read_sql_query('''SELECT * from ritascoolnet_live.dbo.smartDailyZTape Where intZTapeID=6 and Year(dteDate)>=2017 and Year(dteDate)<=2023''',connection)

C:\Users\jharned\AppData\Local\Temp\ipykernel_13828\133753906.py:3: UserWarning: pandas only supports SQLAlchemy connectable (engine/connection) or database string URI or sqlite3 DBAPI2 connection. Other DBAPI2 objects are not tested. Please consider using SQLAlchemy.
  data1=pd.read_sql_query('''SELECT * FROM [dbo].[smartDailySales] Where Year(dteDate)>=2017''',connection)


In [3]:
#Changes the the type of the data from strings to numbers
gc.vchValue=gc.vchValue.astype('int')
gc.rename(columns={'vchValue':'Guest_Count'},inplace=True)

In [4]:
gc['Year']=gc.dteDate.dt.year

In [5]:
gc=gc.merge(data2[['intStoreID','ShopID']],on='intStoreID',how='left')
gc['ShopID']=gc.ShopID.astype('int')

In [6]:
data=data1.merge(data2, on='intStoreID',how='left')
data=data.merge(data4[['intStoreID','CoOpName']],on='intStoreID',how='left')
data['CoOpName']=data.CoOpName.fillna('LSM')

In [7]:
# Creates year and makes intRitasStore ID a numeric 
data['Year']=data.dteDate.dt.year
data['ShopID']=pd.to_numeric(data['ShopID'])

In [8]:
# changes the Directory
os.chdir(r'G:\FinanceReports\2024')
# Kathys files for the list of shops she wants to view
kathy=pd.read_excel('2017 POS Shops.xlsx',sheet_name='Sheet1')
# This is where I will save the files
os.chdir(r'R:\Kathy Deal\New folder')
# List of shops
shops=kathy['Shop ID']
# Df is the dataframe with the years and specific shops we want to view
year=[2017,2018,2019,2020,2021,2022,2023]
df=data[(data.ShopID.isin(shops))&(data.Year.isin(year))&(data.vchProductTypeName!='3rd Party Delivery')]

In [59]:
pd.set_option('display.max_rows', None)
df.groupby(['intProductTypeID','intProductSizeID','vchProductTypeName','vchProductSizeName'])['mnyPrice'].max().reset_index().sort_values(by='vchProductSizeName')

intProductTypeID  intProductSizeID              vchProductTypeName  \
274                53              1182       Cool Stuff Consumer Goods   
35                  3              1250                          Gelati   
20                  1              1249                     Italian Ice   
230                48               395                   Frozen Drinks   
228                48               395                Frozen Beverages   
172                20              1265                          Snacks   
171                20              1265                   Savory Snacks   
174                25               138             Catering (Bulk Ice)   
9                   1                10                     Italian Ice   
37                  3              1256                          Gelati   
22                  1              1255                     Italian Ice   
150                20                27                          Snacks   
149                20                27                   Savory Snacks   
29                  3              1159                          Gelati   
30                  3              1159                          Gelati   
317                59              1138               Cookie Sandwiches   
313                54              1138                       Novelties   
311                54              1138               Cakes & Novelties   
273                53              1181       Cool Stuff Consumer Goods   
339                83               408                            Acai   
340                83               409                            Acai   
139                15               136             Additional Toppings   
125                 6                87                        Blendini   
126                 6                87               Blendini/Concrete   
32                  3              1194                          Gelati   
33                  3              1194                          Gelati   
17                  1              1193                     Italian Ice   
178                25               442             Catering (Bulk Ice)   
179                25               443             Catering (Bulk Ice)   
185                25              1199             Catering (Bulk Ice)   
177                25               441             Catering (Bulk Ice)   
180                25               444             Catering (Bulk Ice)   
13                  1               446                     Italian Ice   
182                25               505             Catering (Bulk Ice)   
12                  1               445                     Italian Ice   
241                48              1155                Frozen Beverages   
240                48              1154                Frozen Beverages   
384                86               483                         Nathans   
363                85              1168              Fresh Baked Treats   
78                  5               438                         Custard   
270                53               518       Cool Stuff Consumer Goods   
159                20               126                   Savory Snacks   
160                20               126                          Snacks   
123                 6                23                        Blendini   
124                 6                23               Blendini/Concrete   
515               117                23                        Blendini   
207                41               135                       Beverages   
366                85              1171              Fresh Baked Treats   
369                85              1172              Fresh Baked Treats   
367                85              1171              Fresh Baked Treats   
370                85              1172              Fresh Baked Treats   
79                  5               439                         Custard   
260                53         

In [60]:
#Grabs Unique Product Names with Product Size Code
names=df[['intProductSizeID','vchProductSizeName']].sort_values(by='intProductSizeID').drop_duplicates(subset=['intProductSizeID'],
                                                                                                keep='last')

In [116]:
for i in list(enumerate(year)): # enumerates the list of shops basically assigns shops numbers 1 through the length of list to
    # be able to easily loop through the list of shops
    pmix=df[(df.Year==i[1])&~(
        df.vchProductTypeName.str.contains('Catering'))].pivot_table(index='intProductSizeID',
                                          columns='ShopID',values='mnyPosSales',
                                          aggfunc='sum',fill_value=0).apply(lambda x:x/x.sum()) # Creates the PMIX spreadsheet
    pmix=pmix.merge(names,on='intProductSizeID',how='left').iloc[:,np.r_[0,-1,1:len(pmix.columns)+1]] # Rearranges the columns
    pmix=pmix.set_index(['intProductSizeID','vchProductSizeName']) # Sets the index
    price=df[(df.Year==i[1])&~(
        df.vchProductTypeName.str.contains('Catering'))].pivot_table(index='intProductSizeID',
                                          columns='ShopID',values='mnyPrice',aggfunc='max',
                                          fill_value=0) # Creates the Retail Price SpreadSheet
    price=price.merge(names,on='intProductSizeID',how='left').iloc[:,np.r_[0,-1,1:len(price.columns)+1]] #Rearranges the columns
    #price=price.set_index(['intProductSizeID','vchProductSizeName'])# Sets the index
    price.loc['Total']=price.iloc[:,2:].sum(axis=0)
    df2=df.groupby(['ShopID','Year'])[['mnyPosSales','intQuantity']].sum().reset_index()#Total Sales and Volume
    gc1=gc.groupby(['ShopID','Year'])['Guest_Count'].sum().reset_index()#Totals Guest Count
    all_df=df2.merge(gc1[['ShopID','Year','Guest_Count']],on=['ShopID','Year'],how='left')#Merges Sales, Volume and Guest Count
    final=all_df[all_df.Year==i[1]].pivot_table(index='ShopID',
                                                values=['mnyPosSales','intQuantity','Guest_Count'],
                                                aggfunc='sum',fill_value=0).iloc[:,[-1,1,0]]# Sales , Volume, GC by Year
    final=final.rename(columns={'mnyPosSales':'Retail_Sales','intQuantity':'Item_Count'})#Renames the columns
    kathy=pd.ExcelWriter('Summary '+str(i[1])+'.xlsx',engine='xlsxwriter')
    final.to_excel(kathy,sheet_name='Summary '+ str(i[1]))
    pmix.to_excel(kathy,sheet_name='PMIX '+ str(i[1]),float_format="%0.3f")
    price.to_excel(kathy,sheet_name='Price '+ str(i[1]),index=False)
    workbook=kathy.book
    worksheet=kathy.sheets['PMIX '+ str(i[1])]
    worksheet_1=kathy.sheets['Price '+ str(i[1])]
    worksheet_2=kathy.sheets['Summary '+ str(i[1])]
    format_1=workbook.add_format({'num_format':'0.00%'})
    format_2=workbook.add_format({'num_format':'$#,##0.00'})
    format_3=workbook.add_format({'num_format':'#,##0'})
    worksheet.set_column('A:B',30)
    worksheet.set_column(1,1000,None,format_1)
    worksheet_1.set_column('A:B',30)
    worksheet_1.set_column(1,1000,None,format_2)
    worksheet_2.set_column('B:B',12, format_2)
    worksheet_2.set_column('C:D',12, format_3)              
    kathy.close()

In [103]:
price=df[(df.Year==2017)&~(
        df.vchProductTypeName.str.contains('Catering'))].pivot_table(index=['intProductSizeID','vchProductTypeName'],
                                          columns='ShopID',values='mnyPrice',aggfunc='max',fill_value=0)
price=price.merge(names,on='intProductSizeID',how='left').iloc[:,np.r_[0,-1,1:len(price.columns)+1]]
# price=price.set_index(['intProductSizeID','vchProductTypeName','vchProductSizeName'])
#price.loc['Total']=price.iloc[:,3:].sum(axis=0)

In [104]:
price

intProductSizeID                                vchProductSizeName     9  \
0                   5                                          Kids Ice  2.99   
1                   6                                           Regular  3.69   
2                   7                                         Large Ice  4.19   
3                   8                                         Quart Ice  6.29   
4                   9                                            Gallon  0.00   
5                  10                                     2 1/2 Gallons  0.00   
6                  19                                           Regular  4.99   
7                  20                                             Large  5.49   
8                  21                                           Regular  4.99   
9                  22                                             Large  5.49   
10                 23                                          Blendini  4.99   
11                 25                                   Regular Pretzel  0.00   
12                 27                                 3 Pretzel Special  0.00   
13                 32                            Extra Custard Upcharge  0.99   
14                 76                                           Regular  5.59   
15                 85                              Regular Frozen Drink  3.99   
16                 86                                Large Frozen Drink  4.49   
17                 87                                          Concrete  5.79   
18                 95                              Cookie Sundae - Kids  0.00   
19                 95                              Cookie Sundae - Kids  0.00   
20                 96                           Cookie Sundae - Regular  0.00   
21                 96                           Cookie Sundae - Regular  0.00   
22                 97                             Cookie Sundae - Large  0.00   
23                 97                             Cookie Sundae - Large  0.00   
24                100                                  Mens Tshirt XXL+  0.00   
25                101                         Womens Tshirt  Small - Xl  0.00   
26                103                                     Plush Ice Guy  0.00   
27                104                                    Bumper Magnets  0.00   
28                105                                        Cooler Bag  0.00   
29                106                                       Kids Sundae  4.99   
30                107                                 Regular SS Sundae  5.49   
31                108                                      Large Sundae  5.99   
32                109                                     Kids Cone/Cup  3.79   
33                110                               Regular SS Cone/Cup  4.29   
34                111                                 Large SS Cone/Cup  4.79   
35                112                                         Sprinkles  0.99   
36                113                                  Waffle Cone/Bowl  0.99   
37                114                                       Waffle Bowl  0.99   
38                115                              Frozen Custard Cakes  0.00   
39                116                   Frozen Cookie Sand Plain 4 Pack  0.00   
40                117                 Frozen Cookie Sand Variety 4 Pack  8.49   
41                120                                           Candles  0.00   
42                121                                        Piping Gel  0.00   
43                122                                    Philly Pretzel  1.25   
44                123                                     Pretzel Braid  0.00   
45                124                             Super Pretzel - Small  0.00   
46                125                           King Size Super Pretzel  0.00   
47                126                          Big Cheese Super Pretzel  0.00   
48                127               

In [120]:
df[(df.Year==2023)&(df.ShopID==628)].groupby(['intProductSizeID','vchProductSizeName']
                                            )[['mnyPosSales','intQuantity','mnyPrice']].agg({'mnyPosSales':'sum',
                                                                                                'intQuantity':'sum',
                                                                                                'mnyPrice':'max'})

mnyPosSales  intQuantity  \
intProductSizeID vchProductSizeName                                             
5                Kids Ice                              3834.0720         1241   
7                Large Ice                            18508.0400         5016   
8                Quart Ice                             6730.3600         1214   
20               Large Gelati                         12254.9300         2317   
23               Blendini                              2048.9100          419   
32               SS Extra Custard                       171.5700          133   
87               Concrete                             18483.9650         3249   
91               Whipped Cream                          103.2000           80   
112              Sprinkles Upcharge                    1004.0900         1271   
113              Waffle Cone/Bowl Upcharge             1172.6000         1066   
122              Philly Pretzel                        1478.5700          743   
128              Coffee Small                            13.2500            5   
129              Coffee Large                             6.7800            2   
135              Ritas Bottled Water                    207.6900          161   
136              Additional Topping                    3926.7600         3044   
261              Individual Custard Cookie Sandwich     457.0740          121   
299              Take Home Custard                      867.1800           83   
316              FDOS Custard Topper                      4.0000            6   
349              SS Custard Pints                       103.2900           11   
454              Ice Flights                           1839.9700          473   
547              Pretzel Cheese Dip                      94.5900           81   
999              Invalid Product Code                  1091.8100           70   
1141             Large Frozen Coffee                    926.8100          169   
1146             Small Frozen Coffee                   1237.5200          248   
1159             5-Layer Gelati                        1789.1100          309   
1198             Ice Fun Pack                          2180.0100          101   
1200             Ice Super Fun Pack                      95.9800            2   
1201             Ice Super Fun Variety Pack            1971.7100           29   
1214             Kids SS Cup/Cone                      2258.3400          566   
1215             Small SS Cup/Cone                    18260.0200         4359   
1216             Large SS Cup/Cone                     8233.0100         1719   
1218             Small SS Sundae                       3980.3800          782   
1219             Large SS Sundae                       1815.1100          319   
1221             Small Brownie Sundae                   889.1400          146   
1222             Large Brownie Sundae                   599.6900           91   
1224             Small Misto                           2309.1225          463   
1225             Large Misto                           3458.7000          630   
1226             Small Frozen Drink                    1657.1400          426   
1227             Large Frozen Drink                    2431.0600          554   
1229             Small Milkshake                       6663.2800         1192   
1230             Large Milkshake                       5663.7000          930   
1246             Small Ice                            27555.2200         8640   
1247             Small Gelati                         14636.3175         3121   
1271             Small Frozen Lemonade                  429.1400           88   
1272             Large Frozen Lemonade                  526.0400           99   

                                                     mnyPrice  
intProductSizeID vchProductSizeName                            
5                Kids Ice                                3.09  
7                Large Ice                           

In [79]:
df[(df.Year==2021)&(df.ShopID==824)].groupby('vchProductSizeName')['mnyPrice'].max()

vchProductSizeName
12 oz Rainbow Gelati                   0.00
12 oz Rainbow Ice                      0.00
2 1/2 Gallon                           0.00
20 oz Rainbow Gelati                   0.00
20 oz Rainbow Ice                      0.00
5-Layer Gelati                         5.69
6-pack Custard Cookie Sandwiches      13.39
Additional Topping                     1.05
Blendini                               5.29
Coffee Small                           0.00
Concrete                               6.29
Frozen Custard Cakes                   0.00
Hot Chocolate Large                    4.69
Ice Flights                            5.19
Ice Fun Pack                          25.99
Ice Super Fun Pack                    55.99
Individual Custard Cookie Sandwich     3.29
Invalid Product Code                   0.00
Kids Ice                               2.69
Kids SS Cup/Cone                       3.09
Kids SS Sundae                         0.00
Large Frozen Drink                     4.49
Large Gelati 

In [13]:
final=all_df.pivot_table(index='ShopID',columns='Year',values=['mnyPosSales','intQuantity','Guest_Count'],aggfunc='sum')
final=final[['mnyPosSales','intQuantity','Guest_Count']]
final=final.rename(columns={'mnyPosSales':'Retail_Sales','intQuantity':'Item_Count'})
final
writer=pd.ExcelWriter('Sales,GC,Volume 2017-2023.xlsx')
final.to_excel(writer,sheet_name='Summary')
workbook=writer.book
worksheet=writer.sheets['Summary']
format_2=workbook.add_format({'num_format':'$#,##0.00'})
format_3=workbook.add_format({'num_format':'#,##0'})
worksheet.set_column('A:A',15)
worksheet.set_column(1,7,13,format_2)
worksheet.set_column(8,25,13,format_3)
writer.close()

In [113]:
    pmix=df[(df.Year==2017)&~(
        df.vchProductTypeName.str.contains('Catering'))].pivot_table(index='intProductSizeID',
                                          columns='ShopID',values='mnyPosSales',
                                          aggfunc='sum',fill_value=0).apply(lambda x:x/x.sum()) # Creates the PMIX spreadsheet
    pmix=pmix.merge(names,on='intProductSizeID',how='left').iloc[:,np.r_[0,-1,1:len(pmix.columns)+1]] # Rearranges the columns
pmix=pmix.set_index(['intProductSizeID','vchProductSizeName']) # Sets the index

In [121]:
df[(df.Year==2017)&(df.ShopID==628)]

intStoreID    dteDate  intRegister  bitAMPM  intProductSizeID  \
4320054        1263 2017-02-10            1    False                 6   
4320055        1263 2017-02-10            1    False                 7   
4320056        1263 2017-02-10            1    False                 8   
4320057        1263 2017-02-10            1    False                19   
4320058        1263 2017-02-10            1    False                20   
4320059        1263 2017-02-10            1    False                21   
4320060        1263 2017-02-10            1    False                23   
4320061        1263 2017-02-10            1    False                76   
4320062        1263 2017-02-10            1    False                87   
4320063        1263 2017-02-10            1    False               108   
4320064        1263 2017-02-10            1    False               110   
4320065        1263 2017-02-10            1    False               111   
4320066        1263 2017-02-10            1    False               112   
4320067        1263 2017-02-10            1    False               114   
4320068        1263 2017-02-10            1    False               136   
4320069        1263 2017-02-11            1    False                 5   
4320070        1263 2017-02-11            1    False                 6   
4320071        1263 2017-02-11            1    False                 7   
4320072        1263 2017-02-11            1    False                 8   
4320073        1263 2017-02-11            1    False                19   
4320074        1263 2017-02-11            1    False                20   
4320075        1263 2017-02-11            1    False                21   
4320076        1263 2017-02-11            1    False                22   
4320077        1263 2017-02-11            1    False                23   
4320078        1263 2017-02-11            1    False                32   
4320079        1263 2017-02-11            1    False                76   
4320080        1263 2017-02-11            1    False                85   
4320081        1263 2017-02-11            1    False               107   
4320082        1263 2017-02-11            1    False               109   
4320083        1263 2017-02-11            1    False               110   
4320084        1263 2017-02-11            1    False               111   
4320085        1263 2017-02-11            1    False               112   
4320086        1263 2017-02-11            1    False               113   
4320087        1263 2017-02-11            1    False               136   
4320088        1263 2017-02-11            1    False              1140   
4320089        1263 2017-02-12            1    False                 5   
4320090        1263 2017-02-12            1    False                 6   
4320091        1263 2017-02-12            1    False                 7   
4320092        1263 2017-02-12            1    False                 8   
4320093        1263 2017-02-12            1    False                19   
4320094        1263 2017-02-12            1    False                20   
4320095        1263 2017-02-12            1    False                21   
4320096        1263 2017-02-12            1    False                22   
4320097        1263 2017-02-12            1    False                76   
4320098        1263 2017-02-12            1    False                85   
4320099        1263 2017-02-12            1    False                86   
4320100        1263 2017-02-12            1    False                87   
4320101        1263 2017-02-12            1    False               107   
4320102        1263 2017-02-12            1    False               108   
4320103        1263 2017-02-12            1    False               109   
4320104        1263 2017-02-12            1    False               110   
4320105        1263 2017-02-12            1    False               111   
4320106        1263 2017-02-12            1    False               112   
4320107      